In [ ]:
!cat /proc/cpuinfo

In [2]:
import sys
sys.path.append('/cycleNew')
!pip install visdom


In [5]:
! npm install -g localtunnel
get_ipython().system_raw('python3 -m pip install visdom')
get_ipython().system_raw('python3 -m visdom.server -port 8097 >> visdomlog.txt 2>&1 &')   
get_ipython().system_raw('lt --port 8097 >> url.txt 2>&1 &')   

              ] - reify:yargs: timing reifyNode:node_modules/localtunnel/n 0ms
changed 22 packages, and audited 23 packages in 2s

3 packages are looking for funding
  run `npm fund` for details

found 0 vulnerabilities


In [6]:
import visdom  


In [7]:
import itertools
import torchvision.transforms as transforms
from torch.utils.data import DataLoader
from torch.autograd import Variable
from PIL import Image
import torch
from utilities import *
from data import *
from options import *
from gener import *
from discr import Discriminator
from residBlock import *

opt = Options(decay_epoch=10,dataroot = 'apple2orange/', n_cpu = 4, cuda = True, n_epochs=50 )

###### Definition of variables ######
# Networks
netG_A2B = Generator(opt.input_nc, opt.output_nc)
netG_B2A = Generator(opt.output_nc, opt.input_nc)
netD_A = Discriminator(opt.input_nc)
netD_B = Discriminator(opt.output_nc)

if opt.cuda:
    netG_A2B.cuda()
    netG_B2A.cuda()
    netD_A.cuda()
    netD_B.cuda()

netG_A2B.apply(weights_init_normal)
netG_B2A.apply(weights_init_normal)
netD_A.apply(weights_init_normal)
netD_B.apply(weights_init_normal)

# Lossess
criterion_GAN = torch.nn.MSELoss()
criterion_cycle = torch.nn.L1Loss()
criterion_identity = torch.nn.L1Loss()

# Optimizers & LR schedulers
optimizer_G = torch.optim.Adam(itertools.chain(netG_A2B.parameters(), netG_B2A.parameters()),
                                lr=opt.lr, betas=(0.5, 0.999))
optimizer_D_A = torch.optim.Adam(netD_A.parameters(), lr=opt.lr, betas=(0.5, 0.999))
optimizer_D_B = torch.optim.Adam(netD_B.parameters(), lr=opt.lr, betas=(0.5, 0.999))

lr_scheduler_G = torch.optim.lr_scheduler.LambdaLR(optimizer_G, lr_lambda=LambdaLR(opt.n_epochs, opt.epoch, opt.decay_epoch).step)
lr_scheduler_D_A = torch.optim.lr_scheduler.LambdaLR(optimizer_D_A, lr_lambda=LambdaLR(opt.n_epochs, opt.epoch, opt.decay_epoch).step)
lr_scheduler_D_B = torch.optim.lr_scheduler.LambdaLR(optimizer_D_B, lr_lambda=LambdaLR(opt.n_epochs, opt.epoch, opt.decay_epoch).step)

# Inputs & targets memory allocation
Tensor = torch.cuda.FloatTensor if opt.cuda else torch.Tensor
input_A = Tensor(opt.batchSize, opt.input_nc, opt.size, opt.size)
input_B = Tensor(opt.batchSize, opt.output_nc, opt.size, opt.size)
target_real = Variable(Tensor(opt.batchSize).fill_(1.0), requires_grad=False)
target_fake = Variable(Tensor(opt.batchSize).fill_(0.0), requires_grad=False)

fake_A_buffer = ReplayBuffer()
fake_B_buffer = ReplayBuffer()

# Dataset loader
transforms_ =[ #transforms.Resize(int(opt.size*1.12), Image.BICUBIC), 
                #transforms.RandomCrop(opt.size), 
                #transforms.RandomHorizontalFlip(),
                transforms.ToTensor(),
                transforms.Normalize((0.5,0.5,0.5), (0.5,0.5,0.5))]
dataloader = DataLoader(ImageDataset(opt.dataroot, transforms_=transforms_, unaligned=True), 
                        batch_size=opt.batchSize, shuffle=True, num_workers=opt.n_cpu)

# Loss plot
logger = Logger(opt.n_epochs, len(dataloader))
###################################


Setting up a new session...


In [10]:


###### Training ######
for epoch in range(opt.epoch, opt.n_epochs):
    for i, batch in enumerate(dataloader):
        # Set model input
        real_A = Variable(input_A.copy_(batch['A']))
        real_B = Variable(input_B.copy_(batch['B']))
        ###### Generators A2B and B2A ######
        optimizer_G.zero_grad()

        # Identity loss
        # G_A2B(B) should equal B if real B is fed
        same_B = netG_A2B(real_B)
        loss_identity_B = criterion_identity(same_B, real_B)*5.0
        # G_B2A(A) should equal A if real A is fed
        same_A = netG_B2A(real_A)
        loss_identity_A = criterion_identity(same_A, real_A)*5.0

        # GAN loss
        fake_B = netG_A2B(real_A)
        pred_fake = netD_B(fake_B)
        loss_GAN_A2B = criterion_GAN(pred_fake, target_real)

        fake_A = netG_B2A(real_B)
        pred_fake = netD_A(fake_A)
        loss_GAN_B2A = criterion_GAN(pred_fake, target_real)
        

        # Cycle loss
        recovered_A = netG_B2A(fake_B)
        loss_cycle_ABA = criterion_cycle(recovered_A, real_A)*10.0

        recovered_B = netG_A2B(fake_A)
        loss_cycle_BAB = criterion_cycle(recovered_B, real_B)*10.0

        # Total loss
        loss_G = loss_identity_A + loss_identity_B + loss_GAN_A2B + loss_GAN_B2A + loss_cycle_ABA + loss_cycle_BAB
        loss_G.backward()
        
        optimizer_G.step()
        ###################################

        ###### Discriminator A ######
        optimizer_D_A.zero_grad()

        # Real loss
        pred_real = netD_A(real_A)
        loss_D_real = criterion_GAN(pred_real, target_real)

        # Fake loss
        fake_A = fake_A_buffer.push_and_pop(fake_A)
        pred_fake = netD_A(fake_A.detach())
        loss_D_fake = criterion_GAN(pred_fake, target_fake)

        # Total loss
        loss_D_A = (loss_D_real + loss_D_fake)*0.5
        loss_D_A.backward()

        optimizer_D_A.step()
        ###################################

        ###### Discriminator B ######
        optimizer_D_B.zero_grad()

        # Real loss
        pred_real = netD_B(real_B)
        loss_D_real = criterion_GAN(pred_real, target_real)
        
        # Fake loss
        fake_B = fake_B_buffer.push_and_pop(fake_B)
        pred_fake = netD_B(fake_B.detach())
        loss_D_fake = criterion_GAN(pred_fake, target_fake)

        # Total loss
        loss_D_B = (loss_D_real + loss_D_fake)*0.5
        loss_D_B.backward()

        optimizer_D_B.step()
        ###################################

        # Progress report (http://localhost:8097)
        losses = {'loss_G': loss_G.item(), 'loss_G_identity': (loss_identity_A.item() + loss_identity_B.item()), 'loss_G_GAN': (loss_GAN_A2B.item() + loss_GAN_B2A.item()),
                    'loss_G_cycle': (loss_cycle_ABA.item() + loss_cycle_BAB.item()), 'loss_D': (loss_D_A.item() + loss_D_B.item())}
        images={'real_A': real_A, 'real_B': real_B, 'fake_A': fake_A, 'fake_B': fake_B}
        logger.log(losses, images)

    # Update learning rates
    lr_scheduler_G.step()
    lr_scheduler_D_A.step()
    lr_scheduler_D_B.step()

    # Save models checkpoints
    torch.save(netG_A2B.state_dict(), 'output/netG_A2B.pth')
    torch.save(netG_B2A.state_dict(), 'output/netG_B2A.pth')
    torch.save(netD_A.state_dict(), 'output/netD_A.pth')
    torch.save(netD_B.state_dict(), 'output/netD_B.pth')
###################################

/opt/conda/lib/python3.7/site-packages/torch/nn/modules/loss.py:528: UserWarning: Using a target size (torch.Size([1])) that is different to the input size (torch.Size([1, 1])). This will likely lead to incorrect results due to broadcasting. Please ensure they have the same size.
  return F.mse_loss(input, target, reduction=self.reduction)


Epoch 001/050 [0001/1019] -- 1
Epoch 001/050 [0002/1019] -- 2
Epoch 001/050 [0003/1019] -- 3ity: 7.0100 | loss_G_GAN: 1.4164 | loss_G_cycle: 14.2149 | loss_D: 0.8087 -- ETA: 2 days, 7:09:27.827697
Epoch 001/050 [0004/1019] -- 4ity: 6.6302 | loss_G_GAN: 0.9782 | loss_G_cycle: 13.5020 | loss_D: 0.8290 -- ETA: 1 day, 16:21:23.198780
Epoch 001/050 [0005/1019] -- 5ity: 6.0243 | loss_G_GAN: 0.8503 | loss_G_cycle: 12.2663 | loss_D: 0.7215 -- ETA: 1 day, 8:57:06.924545
Epoch 001/050 [0006/1019] -- 6ity: 5.7251 | loss_G_GAN: 0.8051 | loss_G_cycle: 11.6922 | loss_D: 0.6731 -- ETA: 1 day, 4:31:04.548370
Epoch 001/050 [0007/1019] -- 7ity: 5.6290 | loss_G_GAN: 0.9074 | loss_G_cycle: 11.4695 | loss_D: 0.6114 -- ETA: 1 day, 1:32:22.552724
Epoch 001/050 [0008/1019] -- 8ity: 5.3787 | loss_G_GAN: 0.8061 | loss_G_cycle: 11.0713 | loss_D: 0.6199 -- ETA: 23:24:58.587189
Epoch 001/050 [0009/1019] -- 9ity: 5.3338 | loss_G_GAN: 0.7963 | loss_G_cycle: 11.0050 | loss_D: 0.5894 -- ETA: 21:48:45.600729
Epoch 001/

In [12]:

import argparse
import sys
import os

import torchvision.transforms as transforms
from torchvision.utils import save_image
from torch.utils.data import DataLoader
from torch.autograd import Variable
import torch

isCuda = True

###### Definition of variables ######
# Networks
netG_A2B = Generator(3,3)
netG_B2A = Generator(3,3)

if isCuda:
    netG_A2B.cuda()
    netG_B2A.cuda()

# Load state dicts
netG_A2B.load_state_dict(torch.load('output/netG_A2B.pth'))
netG_B2A.load_state_dict(torch.load('output/netG_B2A.pth'))

# Set model's test mode
netG_A2B.eval()
netG_B2A.eval()

# Inputs & targets memory allocation
Tensor = torch.cuda.FloatTensor if isCuda else torch.Tensor
input_A = Tensor(1,3,256,256)
input_B = Tensor(1,3,256,256)

# Dataset loader
transforms_ = [ transforms.ToTensor(),
                transforms.Normalize((0.5,0.5,0.5), (0.5,0.5,0.5)) ]
dataloader = DataLoader(ImageDataset('apple2orange/', transforms_=transforms_, mode='test'), 
                        batch_size=1, shuffle=False, num_workers=4)
###################################

###### Testing######

# Create output dirs if they don't exist
if not os.path.exists('output/A'):
    os.makedirs('output/A')
if not os.path.exists('output/B'):
    os.makedirs('output/B')

for i, batch in enumerate(dataloader):
    # Set model input
    real_A = Variable(input_A.copy_(batch['A']))
    real_B = Variable(input_B.copy_(batch['B']))

    # Generate output
    fake_B = 0.5*(netG_A2B(real_A).data + 1.0)
    fake_A = 0.5*(netG_B2A(real_B).data + 1.0)

    # Save image files
    save_image(fake_A, 'output/A/%04d.png' % (i+1))
    save_image(fake_B, 'output/B/%04d.png' % (i+1))

    sys.stdout.write('\rGenerated images %04d of %04d' % (i+1, len(dataloader)))

sys.stdout.write('\n')
###################################

Generated images 0266 of 0266


In [14]:
import argparse
import sys
import os

import torchvision.transforms as transforms
from torchvision.utils import save_image
from torch.utils.data import DataLoader
from torch.autograd import Variable
import torch
isCuda = True

###### Definition of variables ######
# Networks
netG_A2B = Generator(3,3)
netG_B2A = Generator(3,3)

if isCuda:
    netG_A2B.cuda()
    netG_B2A.cuda()

# Load state dicts
netG_A2B.load_state_dict(torch.load('output/netG_A2B.pth'))
netG_B2A.load_state_dict(torch.load('output/netG_B2A.pth'))

# Set model's test mode
netG_A2B.eval()
netG_B2A.eval()

# Inputs & targets memory allocation
Tensor = torch.cuda.FloatTensor if isCuda else torch.Tensor
input_A = Tensor(1,3,256,256)
input_B = Tensor(1,3,256,256)

# Dataset loader
transforms_ = [ transforms.ToTensor(),
                transforms.Normalize((0.5,0.5,0.5), (0.5,0.5,0.5)) ]
dataloader = DataLoader(ImageDataset('apple2orangeSmall/', transforms_=transforms_, mode='test'), 
                        batch_size=1, shuffle=False, num_workers=4)
###################################

###### Testing######

# Create output dirs if they don't exist
if not os.path.exists('output/Atest'):
    os.makedirs('output/Atest')
if not os.path.exists('output/Btest'):
    os.makedirs('output/Btest')

for i, batch in enumerate(dataloader):
    # Set model input
    real_A = Variable(input_A.copy_(batch['A']))
    real_B = Variable(input_B.copy_(batch['B']))

    # Generate output
    fake_B = 0.5*(netG_A2B(real_A).data + 1.0)
    fake_A = 0.5*(netG_B2A(real_B).data + 1.0)

    # Save image files
    save_image(fake_B, 'output/Atest/GANA.png')
    save_image(fake_A, 'output/Btest/GANB.png')
    
    # Generate output
    fake_B2 = 0.5*(netG_A2B(fake_A).data + 1.0)
    fake_A2 = 0.5*(netG_B2A(fake_B).data + 1.0)

    # Save image files
    save_image(fake_A2, 'output/Atest/cycleA.png')
    save_image(fake_B2, 'output/Btest/cycleB.png')
    
    # Generate output
    fake_B = 0.5*(netG_A2B(real_B).data + 1.0)
    fake_A = 0.5*(netG_B2A(real_A).data + 1.0)

    # Save image files
    save_image(fake_A, 'output/Atest/idA.png')
    save_image(fake_B, 'output/Btest/idB.png')
    
    sys.stdout.write('\rGenerated images %04d of %04d' % (i+1, len(dataloader)))

sys.stdout.write('\n')
###################################


Generated images 0001 of 0001
